# 说好不哭（with 五月天阿信）

## 准备

In [1]:
import os
import re
import requests
import json
import random
import time
import datetime
import pprint
import jieba
import jieba.analyse
from bs4 import BeautifulSoup

In [2]:
import pandas as pd
import numpy as np

pd.set_option("display.max_columns", 100)  # 设置显示数据的最大列数，防止出现省略号…，导致数据显示不全
pd.set_option("expand_frame_repr", False)  # 当列太多时不自动换行
pd.set_option('max_colwidth', 500)

In [3]:
def load_config():
    import json
    with open("../config.json") as config:
        return json.load(config)

In [4]:
def mongo_db(db_name):
    '''
    连接MongoDB
    '''
    from pymongo import MongoClient
    client = MongoClient(f'{load_config()["host"]}:27017')
    mongo = client[db_name]
    return mongo


mongo = mongo_db('wont_cry')

In [5]:
def timestamp_to_datetime(time_stamp):
    '''
    时间戳转详细时间
    '''
    import pytz
    tz = pytz.timezone('Asia/Shanghai')
    date_time = datetime.datetime.fromtimestamp(
        time_stamp, tz).strftime('%Y-%m-%d %H:%M:%S')
    return date_time


timestamp_to_datetime(time.time())

'2019-09-23 17:41:12'

## 页面分析

![image](https://raw.githubusercontent.com/hufe09/GitNote-Images/master/image_hosting/image.lfqskrmehnm.png)

In [6]:
url = "https://y.qq.com/n/yqq/album/002gBTVk4JEE2T.html"
requests.get(url)

<Response [200]>

将爬取到的 HTML 存储在本地，打开发现是这样。
![image](https://raw.githubusercontent.com/hufe09/GitNote-Images/master/image_hosting/image.r38g4cdslh.png)

In [7]:
soup = BeautifulSoup(requests.get(url).content, "lxml")
title = soup.find("h1", class_="data__name_txt").get('title')
album_img_url = f"https:{soup.find('img', id='albumImg').get('src')}"
data_info_item = soup.find("ul", class_="data__info").find_all(
    "li", "data_info__item")
for i, j in list(enumerate(data_info_item)):
    if i == 0:
        genre = j.contents[0]
    if i == 1:
        language = j.contents[0]
    if i == 2:
        publish_time = j.contents[0]
    if i == 3:
        company = j.a.string


title, album_img_url, genre, language, publish_time, company

('说好不哭（with 五月天阿信）',
 'https://y.gtimg.cn/music/photo_new/T002R300x300M000002gBTVk4JEE2T_2.jpg?max_age=2592000',
 '流派：Pop 流行',
 '语种：国语',
 '发行时间：2019-09-16',
 '杰威尔音乐有限公司')

## 专辑信息

上面的页面解析可以轻松获取到静态的这些信息，但是想爬取已售专辑张数，会发现根本没有任何相关信息。所以我猜测这部分数据是 js 通过 Ajax 加载的，所以去观察了访问后台的请求 url。

打开了这个链接 `y.gtimg.cn/music/portal/js/v4/album_eeee476.js?max_age=31536000` 发现，竟然有意外收获，一切跟猜想一样。

![image](https://raw.githubusercontent.com/hufe09/GitNote-Images/master/image_hosting/image.i16zxvmft.png)

通过1.找到2.再找到3.。最终找到了下面的这个 url。一切数据完整地展现在眼前，那还等什么，开取呗。

In [8]:
url = 'https://c.y.qq.com/v8/fcg-bin/musicmall.fcg?cmd=get_album_buy_page&albumid=7876962'

``` python
print(requests.get(url).text)
# MusicJsonCallback({"code":0,...,"uin":"0"})
```

json 转化为 dict 之前，需要把前面的 'MusicJsonCallback()' 去掉。

In [ ]:
wont_cry_json = json.loads(requests.get(url).text[18:-1])
# wont_cry_json

![image](https://raw.githubusercontent.com/hufe09/GitNote-Images/master/image_hosting/image.btn0riu2qk.png)

从 json 据唱获取下面数据: 专辑ID，专辑MID，专辑名，唱片公司，封面图，发行时间，价格（3元）

In [10]:
wont_cry_info = wont_cry_json['data']
wont_cry_info['album_id'],  wont_cry_info['album_mid'], wont_cry_info[
    'album_name'], wont_cry_info['companyname'], wont_cry_info['headpiclist'][0]['picurl'], wont_cry_info['publictime'], int(wont_cry_info['price']/100)

('7876962',
 '002gBTVk4JEE2T',
 '说好不哭（with 五月天阿信）',
 '杰威尔音乐有限公司',
 'http://y.gtimg.cn/music/photo_new/T002R500x500M000002gBTVk4JEE2T.jpg',
 '2019-09-16',
 3)

## 销售信息

In [11]:
sale_info = wont_cry_json['data']['sale_info']
sale_info

{'actid': 381,
 'album_count': 8082959,
 'albumid': 7876962,
 'ident_level': 9,
 'sale_by_song': 0,
 'sale_money': 24248877,
 'song_count': 0,
 'total_song_count': 8082959,
 'unit': '张'}

截止目前，卖出去800万多张，价值2420万多。

## 评论

### 评论总数

评论也是一样，通过 Ajax 获取的，所以直接找就是了。没错，就是下面的这个 url。

```
https://c.y.qq.com/base/fcgi-bin/fcg_global_comment_h5.fcg?g_tk=5381&loginUin=0&hostUin=0&format=json&inCharset=utf8&outCharset=GB2312&notice=0&platform=yqq.json&needNewCode=0&cid=205360772&reqtype=2&biztype=2&topid=7876962&cmd=8&needmusiccrit=0&pagenum=0&pagesize=25&lasthotcommentid=&domain=qq.com&ct=24&cv=10101010'
```

拿到之后，觉得它有点长，尝试能不能去掉一些参数，经过测试，最终留下的参数如下。

具体的评论信息，此链接相比较之前不同的是 `&cmd=8`、`&pagesize=25` 和 `&pagenum=3` 三个参数，`cmd` 为展示形式，`pagesize` 为每页评论数，`pagenum` 为页数。（后面爬取的时候只改变页数就可以，其他保持不变。）

In [79]:
url = 'https://c.y.qq.com/base/fcgi-bin/fcg_global_comment_h5.fcg?format=json&platform=yqq.json&biztype=2&topid=7876962&cmd=4'
comment_total_json = json.loads(requests.get(url).text)
comment_total_json

{'batch_commenttotal': [{'commenttotal': '19775', 'topid': '7876962'}],
 'biztype': '2',
 'code': 0,
 'commenttotal': 19775,
 'subcode': 0,
 'topid': '7876962'}

### 爬取评论

In [13]:
url = 'https://c.y.qq.com/base/fcgi-bin/fcg_global_comment_h5.fcg?format=json&platform=yqq.json&biztype=2&topid=7876962&cmd=8&pagesize=25&pagenum=3'
# pprint.pprint(json.loads(requests.get(url).text))

评论列表在 `{'comment': {'commentlist': []}}` 中, 取其中一个评论数据进行分析。

``` python
pprint.pprint(json.loads(requests.get(url).text)['comment']['commentlist'][0])
```
``` json
 {'avatarurl': 'http://thirdqq.qlogo.cn/g?b=sdk&k=N4f2HOqIstddptScZsntHw&s=140&t=1563950324',
  'commentid': 'album_7876962_1602347020_1568990323_3266898298_1568992600',
  'commit_state': 2,
  'enable_delete': 0,
  'encrypt_rootcommentuin': 'oKCzowoP7inAon**',
  'encrypt_uin': 'oi-s7wcqNe-qNn**',
  'identity_pic': '',
  'identity_type': 0,
  'is_hot': 1,
  'is_hot_cmt': 0,
  'is_medal': 1,
  'is_stick': 0,
  'ispraise': 0,
  'middlecommentcontent': [{'encrypt_replyeduin': '7wviNKcz7Kvl',
    'encrypt_replyuin': 'oi-s7wcqNe-qNn**',
    'reply_identity_pic': '',
    'reply_identity_type': 0,
    'replyed_identity_pic': '',
    'replyed_identity_type': 0,
    'replyednick': '@浅笑丷梨花落゛',
    'replyeduin': '643980547',
    'replynick': '@鷄白飯加个蛋',
    'replyuin': '3266898298',
    'subcommentcontent': '买了就永久可以下载',
    'subcommentid': 'album_7876962_1602347020_1568990323_3266898298_1568992600'},
   {'encrypt_replyeduin': 'oKCzowoP7inAon**',
    'encrypt_replyuin': '7wviNKcz7Kvl',
    'reply_identity_pic': '',
    'reply_identity_type': 0,
    'replyed_identity_pic': '',
    'replyed_identity_type': 0,
    'replyednick': '@\u3000',
    'replyeduin': '1602347020',
    'replynick': '@浅笑丷梨花落゛',
    'replyuin': '643980547',
    'subcommentcontent': '买过之后可以下载MP3格式 的吗',
    'subcommentid': 'album_7876962_1602347020_1568990323_643980547_1568992403'}],
  'nick': '鷄白飯加个蛋',
  'permission': 0,
  'praisenum': 0,
  'root_enable_delete': 0,
  'root_identity_pic': '',
  'root_identity_type': 0,
  'root_is_stick': 0,
  'rootcommentcontent': '可惜3块钱了',
  'rootcommentid': 'album_7876962_1602347020_1568990323',
  'rootcommentnick': '@\u3000',
  'rootcommentuin': '1602347020',
  'score': 0,
  'taoge_topic': '',
  'taoge_url': '',
  'time': 1568992600,
  'uin': '3266898298',
  'user_type': '',
  'vipicon': 'http://imgcache.gtimg.cn/music/icon/v1/h5/svip4.png'},
```

这里面信息很多，挑一些需要用到的。具体为下面这几个信息：
- comment_id，评论ID，作为唯一标识
- content，评论内容
- user_id，用户ID
- reply，回复
- nick，用户昵称
- praise_num，点赞数
- time，时间戳
- vip_level，VIP等级，根据'vipicon'中的命名来判断

评论分为两种情况：直接评论，和回复评论，很容易区分。如果是直接评论，`middlecommentcontent` 为 `None`，如果是回复评论：`middlecommentcontent` 内容为json。

`praise_num`, `nick`, `time`, `vip_level`这几个维度，两种评论数据源都相同。

针对直接评论：
- rootcommentcontent，评论内容
- uin，用户ID，'1925144526'
- rootcommentid，评论的ID格式为 `album_7876962_1925144526_1569065217`，是由 `album_专辑ID_用户ID_随机数` 构成，我选择把 **用户ID_随机数** 作为 comment_id
- reply，非回复，则记录为0

针对回复评论：
- subcommentid，'album_7876962_1602347020_1568990323_3266898298_1568992600'，`album_专辑ID_被回复用户ID_当前用户ID_随机数` 构成，我选择把 **当前用户ID_随机数** 作为 comment_id
- subcommentcontent，评论内容
- replyuin，用户ID，'3266898298'
- reply，被评论的那条的评论ID

In [14]:
def comments_to_mongo(url):
    '''
    将此url信息存入MongoDB
    '''
    comments_to_mongo_list = []
    comment_list = json.loads(requests.get(url).text)['comment']['commentlist']
    for comment in comment_list:
        comment_detail = {}
        if comment['middlecommentcontent'] == None:
            comment_detail['comment_id'] = ''.join(
                comment['rootcommentid'].split('_')[-2::])
            comment_detail['content'] = comment['rootcommentcontent']
            comment_detail['reply'] = '0'
            comment_detail['user_id'] = comment['uin']
        else:
            reply_comment = comment['middlecommentcontent'][0]
            comment_detail['comment_id'] = ''.join(
                reply_comment['subcommentid'].split('_')[-2::])
            comment_detail['content'] = reply_comment['subcommentcontent']
            comment_detail['reply'] = ''.join(
                comment['rootcommentid'].split('_')[-2::])
            comment_detail['user_id'] = reply_comment['replyuin']

        comment_detail['nick'] = comment['nick']
        comment_detail['time'] = timestamp_to_datetime(comment['time'])
        comment_detail['vip_level'] = comment['vipicon'].split(
            "/")[-1][-5] if (comment['vipicon']) else 0
        comment_detail['praise_num'] = comment['praisenum']
        comments_to_mongo_list.append(comment_detail)
    mongo.comments.insert_many(comments_to_mongo_list)
#     pprint.pprint(comments_to_mongo_list)

In [15]:
# 获取总评论数
comment_total_num = json.loads(requests.get(url).text)[
    'comment']['commenttotal']

comment_total_num, len(json.loads(requests.get(url).text)[
                       'comment']['commentlist'])

(19770, 25)

In [16]:
def create_urls_generator(num):
    '''
    url 迭代器
    '''
    for i in range(num):
        yield f"https://c.y.qq.com/base/fcgi-bin/fcg_global_comment_h5.fcg?format=json&platform=yqq.json&reqtype=2&biztype=2&topid=7876962&cmd=8&pagesize=25&pagenum={i}"


page_num = int(comment_total_num / 25 + 1)
urls_generator = create_urls_generator(page_num)

In [17]:
def main():
    mongo = mongo_db('wont_cry')
    mongo.comments.drop()
    for url in urls_generator:
        comments_to_mongo(url)
    print("Finished.")


# %time main()

Finished.
CPU times: user 20 s, sys: 1.74 s, total: 21.7 s
Wall time: 3min 9s


## 数据争论

### 获取数据

In [18]:
def query_from_mongo(query={}):
    '''
    从MongoDB查询数据
    '''
    try:
        find_res = mongo.comments.find(query)
        # 判断是否有查询结果
        count = mongo.comments.count_documents(query, skip=0)
        if count:
            return pd.DataFrame(find_res).drop("_id", axis=1)
        else:
            print("No results.")
    except Exception as e:
        print(e)

In [19]:
query = {"comment_id": "250755371568648733"}
query_from_mongo(query)

comment_id             content   nick  praise_num reply                 time   user_id vip_level
0  250755371568648733  哭…[em]e401148[/em]  Ё v ａ           0     0  2019-09-16 23:45:33  25075537         1

In [20]:
comments_df = query_from_mongo()
comments_df.time = pd.to_datetime(comments_df.time)
comments_df.sample(10)

comment_id                                                             content        nick  praise_num                 reply                time              user_id vip_level
11607  11529215048149284961568647589                                                                 听哭了  Gden     °           0                     0 2019-09-16 23:26:29  1152921504814928496         5
8210            22475899691568649287               暗恋时《等你下课》\n热恋时《告白气球》\n分手时《不爱我就拉倒》\n分手后《说好不哭》\n还是那么懂青春         本来~           2                     0 2019-09-16 23:54:47           2247589969         0
12184           24253835371568647399                                                             哈哈，能听了！     水晶小熊不忧伤           0                     0 2019-09-16 23:23:19           2425383537         7
13636           12646701641568647064                                                           听不了啊现在 服了          假面           1                     0 2019-09-16 23:17:44           1264670164         0
7892             4255561941568649564                                       一直在崩溃，根本没有打开过[em]e400867[/em]          玉儿           0                     0 2019-09-16 23:59:24            425556194         0
612    11529215047358298941568985859                                                    多余多年的粉丝来说这首歌我给差评          段炼           2                     0 2019-09-20 21:24:19  1152921504735829894         0
12749            5782311031568647252                                                                 最爱伦    Mr.J°●︿●           0                     0 2019-09-16 23:20:52            578231103         0
8430             9589770461568649112                                                                我好想你        M.　　           1                     0 2019-09-16 23:51:52            958977046         0
447              2299306211569050309  他自己也很意外，所以在Mv女主举着话题第一的牌子，歌里正好唱到 :都这个时候你还在意别人是怎么看我的[em]e400867[/em]       ﹎_╋﹎_           1  33415886211568646369 2019-09-21 15:18:29            229930621         0
571              6439805471568992403                                                    买过之后可以下载MP3格式 的吗     浅笑丷梨花落゛           1  16023470201568990323 2019-09-20 23:13:23            643980547         0

In [21]:
comments_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19770 entries, 0 to 19769
Data columns (total 8 columns):
comment_id    19770 non-null object
content       19770 non-null object
nick          19770 non-null object
praise_num    19770 non-null int64
reply         19770 non-null object
time          19770 non-null datetime64[ns]
user_id       19770 non-null object
vip_level     19770 non-null object
dtypes: datetime64[ns](1), int64(1), object(6)
memory usage: 1.2+ MB


### 检查重复值

In [22]:
comments_df[comments_df.comment_id.duplicated()]

Empty DataFrame
Columns: [comment_id, content, nick, praise_num, reply, time, user_id, vip_level]
Index: []

In [23]:
# 去重
comments_df = comments_df.drop_duplicates(['comment_id'], keep="first")

在爬取过程中以及对 `comment_id` 进行唯一化操作，如果有重复很有可能是分页过程正好重叠了。

## 数据分析

### 统计评论中的emoji

emoji表情在日常生活中已经非常常见，在评论中也非常常见。但是，QQ音乐评论中是以图片形式显示的，在我们爬到的数据中，是字符串，无法显示，所以要清洗掉。
在清洗之前，先来统计一下这些emoji在评论中出现的次数。

![image](https://raw.githubusercontent.com/hufe09/GitNote-Images/master/image_hosting/image.dgg6m29zoyp.png)

In [24]:
def download_file(url, file_path):
    '''
    从网络下载文件
    '''
    import requests
    r = requests.get(url)
    try:
        with open(file_path, 'wb') as f:
            f.write(r.content)
            f.close()
            return file_path
    except Exception as e:
        print(e)

In [25]:
emoji_s = comments_df.content.apply(
    lambda x: re.findall(r"\[em\]e\d{6}\[\/em\]", x))
emoji_s[emoji_s.map(len) > 0]
emoji_list = []
for i in emoji_s[emoji_s.map(len) > 0]:
    for j in i:
        emoji_list.append(j[4:11])
        
emoji_urls = []
for emoji in emoji_list:
    url = f'https://y.gtimg.cn/mediastyle/global/emoji/img/{emoji}.png'
    emoji_urls.append((emoji, url))
    
emoji_df = pd.DataFrame(emoji_urls, columns=['emoji', 'url'])
emoji_df.head()

emoji                                                         url
0  e400823  https://y.gtimg.cn/mediastyle/global/emoji/img/e400823.png
1  e400126  https://y.gtimg.cn/mediastyle/global/emoji/img/e400126.png
2  e401137  https://y.gtimg.cn/mediastyle/global/emoji/img/e401137.png
3  e401383  https://y.gtimg.cn/mediastyle/global/emoji/img/e401383.png
4  e400824  https://y.gtimg.cn/mediastyle/global/emoji/img/e400824.png

In [74]:
emoji_counts_df = pd.DataFrame(emoji_df.emoji.value_counts())
emoji_counts_df = emoji_counts_df.rename(
    columns={'emoji': 'counts'})

emoji_counts_df['emoji'] = emoji_counts_df.index
emoji_counts_df.head()

counts    emoji
e400867    1555  e400867
e401236     599  e401236
e400824     372  e400824
e400825     335  e400825
e400835     259  e400835

In [75]:
emoji_df_uni = emoji_df.drop_duplicates(['emoji'], keep="first")
emoji_df_uni.head()

emoji                                                         url
0  e400823  https://y.gtimg.cn/mediastyle/global/emoji/img/e400823.png
1  e400126  https://y.gtimg.cn/mediastyle/global/emoji/img/e400126.png
2  e401137  https://y.gtimg.cn/mediastyle/global/emoji/img/e401137.png
3  e401383  https://y.gtimg.cn/mediastyle/global/emoji/img/e401383.png
4  e400824  https://y.gtimg.cn/mediastyle/global/emoji/img/e400824.png

In [76]:
emoji_count = pd.merge(emoji_df_uni,
                      emoji_counts_df, how='left', on='emoji').sort_values(by='counts', ascending=False)

emoji_count.head(20)

emoji                                                         url  counts
19  e400867  https://y.gtimg.cn/mediastyle/global/emoji/img/e400867.png    1555
14  e401236  https://y.gtimg.cn/mediastyle/global/emoji/img/e401236.png     599
4   e400824  https://y.gtimg.cn/mediastyle/global/emoji/img/e400824.png     372
8   e400825  https://y.gtimg.cn/mediastyle/global/emoji/img/e400825.png     335
11  e400835  https://y.gtimg.cn/mediastyle/global/emoji/img/e400835.png     259
0   e400823  https://y.gtimg.cn/mediastyle/global/emoji/img/e400823.png     200
32  e401148  https://y.gtimg.cn/mediastyle/global/emoji/img/e401148.png     196
48  e400116  https://y.gtimg.cn/mediastyle/global/emoji/img/e400116.png     196
2   e401137  https://y.gtimg.cn/mediastyle/global/emoji/img/e401137.png     179
7   e400832  https://y.gtimg.cn/mediastyle/global/emoji/img/e400832.png     149
25  e400408  https://y.gtimg.cn/mediastyle/global/emoji/img/e400408.png     146
5   e400848  https://y.gtimg.cn/mediastyle/global/emoji/img/e400848.png     132
17  e400837  https://y.gtimg.cn/mediastyle/global/emoji/img/e400837.png     128
53  e400873  https://y.gtimg.cn/mediastyle/global/emoji/img/e400873.png     126
10  e400836  https://y.gtimg.cn/mediastyle/global/emoji/img/e400836.png     123
27  e400850  https://y.gtimg.cn/mediastyle/global/emoji/img/e400850.png      99
12  e400826  https://y.gtimg.cn/mediastyle/global/emoji/img/e400826.png      79
73  e400834  https://y.gtimg.cn/mediastyle/global/emoji/img/e400834.png      75
29  e400875  https://y.gtimg.cn/mediastyle/global/emoji/img/e400875.png      74
6   e400831  https://y.gtimg.cn/mediastyle/global/emoji/img/e400831.png      68

### 可视化库 ploty

In [29]:
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots

In [30]:
import plotly.offline
import cufflinks as cf
%reload_ext autoreload
%autoreload 2
# We set the all charts as public
# Offline mode
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True, theme='ggplot')

In [31]:
qq_music_logo = [
    dict(
        source="https://raw.githubusercontent.com/hufe09/GitNote-Images/master/image_hosting/data_origin.asv46cc9pjl.png",
        xref="paper",
        yref="paper",
        x=1,
        y=1,
        sizex=0.1,
        sizey=0.2,
        xanchor="right",
        yanchor="bottom"
    )
]

下载emoji图片

In [32]:
for i in emoji_count.head(20).index:
    url = emoji_count.loc[i].url
    file_path = f'./emoji/{emoji_count.loc[i].emoji}.png'
    download_file(url, file_path)
print("Download finished.")

Download finished.


准备绘图的图标和文字标注

In [77]:
emoji_imgs = []
emoji_annotations = []
for j, i in enumerate(emoji_count.head(20).index):
    url = emoji_count.loc[i].url
    file_path = f'./emoji/{emoji_count.loc[i].emoji}.png'
    emoji_x = j*(1/20)+ 0.02
    emoji_y = 0.05+emoji_count.loc[i].counts / 1600
    emoji_imgs.append(
        dict(
            source=file_path,
            xref="paper",
            yref="paper",
            layer='above',
            x=emoji_x,
            y=emoji_y,
            sizex=0.08,
            sizey=0.08,
            xanchor="center",
            yanchor="top",
        ))
    emoji_annotations.append(
        dict(
            text=str(emoji_count.loc[i].counts),
            x=emoji_x,
            y=emoji_y+0.001,
            xref="paper",
            yref="paper",
            showarrow=False,
            opacity=1,
        ))
#     download_file(url, file_path)

In [78]:
trace1 = go.Scatter(
    x=emoji_count.head(20).emoji,
    y=emoji_count.head(20).counts,
    text=emoji_count.head(20).counts,
    textposition='top left',
    mode="none",
    marker=dict(
        size=20,
        color='#2CB56B'
    )
)
data = [trace1]
layout = go.Layout(
    template='ggplot2',
    images=qq_music_logo+emoji_imgs,
    annotations = emoji_annotations,
    title="emoji 表情统计",
    xaxis=dict(visible=False),
)

fig = go.Figure(data=data, layout=layout)
fig.show()

>啥也别说了，从发歌到现在，我连歌曲都没刷新出来，搜索功能都直接崩溃,不愧是周董，当之无愧的天王
>    <img src="//y.gtimg.cn/mediastyle/global/emoji/img/e400824.png"><img src="//y.gtimg.cn/mediastyle/global/emoji/img/e401236.png">


>世界上最浪漫的事情是什么呀？
>
>当然是带上你的那个她（他）去看一次周杰伦的演唱会啊！毕竟那是自己的整个青春️<img src="//y.gtimg.cn/mediastyle/global/emoji/img/e401148.png">

### 评论内容清洗

In [37]:
emoji = re.compile(r"\[em\]e\d{6}\[\/em\]")
pattern = re.compile(r"[\s+\/_\\n$%^*()?+\"\']+|[+——~@#￥%&*]+")

将表情和一些符号剔除掉。

In [38]:
comments_df.content = comments_df.content.replace(emoji, "")
comments_df.content = comments_df.content.replace(pattern, "")
comments_df.sample(10)

comment_id                             content      nick  praise_num                          reply                time              user_id vip_level
4868   11529215048604138831568683072                           你在，我们一直在！        星晴           0                              0 2019-09-17 09:17:52  1152921504860413883         0
14796           27709094121568646889  我爱你，qzw，，啊啊，我也不知道为什么要在这说我爱你反正我爱你啊!        ……           1                              0 2019-09-16 23:14:49           2770909412         0
5813             5976947551568661299                                 不可以     Gakki           1            2805316801568659553 2019-09-17 03:14:59            597694755         0
2144             5405853601568735250                       不管怎么说，其实我还爱你。      　              3                              0 2019-09-17 23:47:30            540585360         7
16918           27290154741568646651                                啊啊啊啊   ヅ纸上的青春彡           0                              0 2019-09-16 23:10:51           2729015474         0
7972            12457972041568649486                               心疼你几秒   Yesaner           0  11529215047937498681568649419 2019-09-16 23:58:06           1245797204         0
14140           12069249521568646979                             进不去进不去啊  Promise丶           0                              0 2019-09-16 23:16:19           1206924952         5
9060   11529215049400206681568648663                        怪不得有种彩虹知足的感觉      蚂蚁绊象           1                              0 2019-09-16 23:44:23  1152921504940020668         0
15749           22399945851568646774               他的歌真的是从小听到大，还有，超爱徐海英呀         念           0                              0 2019-09-16 23:12:54           2239994585         0
4851            19791823281568683195                     今天第一件事，和男朋友一起分享      夏日限定           0                              0 2019-09-17 09:19:55           1979182328         1

### 评论词云绘制

In [50]:
comment_str = ' '.join(comments_df.content)
# 去标点符号
comment_str = re.sub(
    r"[0-9\s+\.\!\/_,$%^*()?;；:-【】+\"\']+|[+——！，;:。？、~@#￥%……&*（）]+", "", comment_str)

#### 对句子进行分词

In [51]:
def stopwordslist(filepath):
    '''
    创建停用词list
    '''
    stopwords = [line.strip() for line in open(
        filepath, 'r', encoding='utf-8').readlines()]
    return stopwords


def seg_sentence(sentence):
    '''
    对句子进行分词
    '''
    sentence_seged = jieba.cut(sentence.strip())
    stopwords = stopwordslist("../chinese_stop_words.txt")  # 这里加载停用词的路径
    stopwords.extend([' ', '周', '杰伦'])
    for word in sentence_seged:
        if word not in stopwords:
            if word != '\t':
                yield word

#### 统计词频

In [52]:
count_dict = {}
for word in seg_sentence(comment_str):
    if word in count_dict:
        count_dict[word] += 1
    else:
        count_dict[word] = 1
count_dict = list(count_dict.items())
count_dict.sort(key=lambda x: x[1], reverse=True)

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 1.529 seconds.
Prefix dict has been built succesfully.


In [53]:
count_dict_df = pd.DataFrame(count_dict, columns=['word', 'counts'])
count_dict_df.head(20).T

0     1     2     3     4     5     6     7     8    9    10   11   12   13   14   15   16   17   18   19
word       听   周杰伦    青春     哭   演唱会    喜欢    音乐    说好     爱   好听   终于  服务器   真的   评论   周董   听到    崩   不哭   专辑  带你去
counts  3320  2517  1952  1512  1175  1127  1059  1052  1018  866  681  657  645  602  559  555  523  514  513  454

In [54]:
symbol_list = ['circle']*5+['circle-dot']*5+['diamond']*5+['square']*5
data = [go.Scatter(
    x=count_dict_df[:20].word,
    y=count_dict_df[:20].counts,
    text=count_dict_df[:20].counts,
    mode='markers+text',
    textposition="top center",
    textfont=dict(size=14),
    marker=dict(
        size=count_dict_df[:20].counts/40,
        color=[i for i in range(20)],
        colorscale='Viridis',
        symbol=symbol_list,
        opacity=0.5,
    )
)
]
layout = go.Layout(template='ggplot2',
                   images=qq_music_logo,
                   title="词频Top20",
                   yaxis=dict(title='词频'))
fig = go.Figure(data=data, layout=layout)
fig.show()

#### 基于 TF-IDF 算法的关键词抽取

In [55]:
jieba.analyse.set_stop_words("../chinese_stop_words.txt")
word_weight = jieba.analyse.extract_tags(
    comment_str, topK=1000, withWeight=True, allowPOS=('ns', 'n', 'vn', 'v'))

In [56]:
word_weight_df = pd.DataFrame(word_weight, columns=['word', 'weight'])
word_weight_df.head(20).T

0        1        2         3         4         5         6         7         8          9          10         11         12         13         14         15         16         17         18         19
word          青春      演唱会       说好        好听        音乐        喜欢       服务器        专辑       带你去         评论         首歌         单曲        进不去         听到         新歌         等到         加油         崩溃         听歌        打不开
weight  0.337611  0.27481  0.18935  0.164386  0.153723  0.140717  0.135394  0.124313  0.100562  0.0893273  0.0875709  0.0753535  0.0731272  0.0697432  0.0636059  0.0612568  0.0603558  0.0574372  0.0562768  0.0474383

In [57]:
data = [go.Scatter(

    x=word_weight_df[:20].word,
    y=word_weight_df[:20].weight,
    text=[f'{i:.3f}' for i in word_weight_df[:20].weight],
    mode='markers+text',
    textposition="top center",
    textfont=dict(size=14),
    marker=dict(
        size=word_weight_df[:20].weight*220,
        color=[i for i in range(20)],
        colorscale='Viridis',
        symbol=symbol_list,
        opacity=0.5,
    )
)
]
layout = go.Layout(template='ggplot2',
                   images=qq_music_logo,
                   title="权重Top20",
                   yaxis=dict(title='权重'))
fig = go.Figure(data=data, layout=layout)
fig.show()

#### 绘制词云

In [58]:
from pyecharts import options as opts
from pyecharts.charts import Page, WordCloud
from pyecharts.globals import SymbolType


def word_cloud_diamond(words) -> WordCloud:
    """
    pyecharts 绘制评论词云
    :param words: [(word, counts)] 元组列表
    :return: pyecharts wordcloud 对象
    """
    c = (WordCloud().add("",
                         words,
                         word_size_range=[10, 50],
                         shape=SymbolType.ROUND_RECT).set_global_opts(
                             title_opts=opts.TitleOpts(title="《说好不哭》QQ音乐评论")))
    return c

根据词频绘制

In [59]:
Page().add(word_cloud_diamond(count_dict)).render_notebook()

根据权重绘制

In [60]:
Page().add(word_cloud_diamond(word_weight)).render_notebook()

青春、演唱会、服务器、说好、好听等词是同学们最常用的词。
>如果有一天 我带你去看周杰伦的演唱会 那么你一定对我很重要 因为我带你去看的 是我一整个青春

### 根据点赞数分析

In [61]:
praise_count = comments_df.sort_values(
    by='praise_num', ascending=False).head(20)
praise_count = praise_count[praise_count.praise_num > 100]
praise_count

comment_id                                                                                                                                                                                                                                                                                                     content      nick  praise_num reply                time              user_id vip_level
19764            3732625331568646264                                                                                                                                                                                                                                                                  如果有一天我带你去看周杰伦的演唱会那么你一定对我很重要因为我带你去看的是我一整个青春         陈       18151     0 2019-09-16 23:04:24            373262533         0
18319           19721474481568646488                                                                                                                                                                                                                                                              见过让一个软件崩服务器的人吗？他就是周杰伦！出道19年发一个曲子依旧火爆的周杰伦，音乐皇帝！         白       10896     0 2019-09-16 23:08:08           1972147448         2
19769  11529215049567955201568646262                                                                                                                                                                                                                                                                    满怀期待等候多时并且重新下回了qq音乐就是为了此时此刻第一时间来听我伦新歌！！！        小懒        5225     0 2019-09-16 23:04:22  1152921504956795520         0
19763           27172464991568646265                                                                                                                                                                                     等了这么久，终于等到了今天，虽然不是新专但我也一样心满意足，是鸽鸽让我爱上音乐，让我也想和他一样弹钢琴，也是鸽鸽教我要听妈妈的话。我从三岁开始听杰伦的歌，如果说人生中的老师有三个，那么我人生中的老师就是爸妈和杰伦以及让我变得更好的老师们！       伽蓝雨        3381     0 2019-09-16 23:04:25           2717246499         1
16450           27255356511568646699                                                                                                                                                你知道吗？周董…多少人为了你开通了QQ音乐的绿砖多少人在你的新歌发布之前不换网名不改个性签名不换头像多少人为了你等到什么时候都愿意你是多少人的青春你是多少人的偶像你是多少人的期盼你是多少人愿意守护的人你又是多少人的希望又有多少人一直爱着你又有多少人一直等着你无论别人是谁无论别人喜欢谁我不管……我喜欢的是，周杰伦        李现        3125     0 2019-09-16 23:11:39           2725535651         0
19649           25469348401568646296                                                                                                                                                                                                                                                    “世界上最浪漫的事情是什么呀？”“当然是带上你的那个她（他）去看一次周杰伦的演唱会啊！毕竟那是自己的整个青春️”         ⁢        3049     0 2019-09-16 23:04:56           2546934840         6
19100           33415886211568646369                                                                                               万众瞩目，看看谁回来了称他为现象级歌手都不过分，粉丝最起码涵盖80后到00后三个年龄段，甚至包括好多成名了的艺人，前段时间随便给后辈玩玩，一号召一堆人给他打榜，甚至包括各种明星！流行歌手不敢说，我就知道当初有好多现在成名了的说唱歌手，有13都是因为听了他的歌才决定玩说唱的我就不用说了，永远忘不了曾经攒下午饭钱买他卡带的日子说好不哭，有新歌我们肯定不哭，只要你周杰伦发了新歌，我绝对第一时间支持，respect     💎九局下半        2122     0 2019-09-16 23:06:09           3341588621         0
15868           22797584691568646762                                       当篮球从手中滑落，当练习滑板一次次摔倒，是你让我疲惫心灵得到短暂休憩；当每个失眠的深夜，是你带给我温暖，让我陷入最美好的梦想；当第一次牵起等我下课的女孩，是你的音乐带给我最甜蜜的浪漫，如果说最难忘的是谁？那么就是我永远无法抹去的记忆！一直也忘不了你说的那句：“不管什么时候，什么地点，我希望我的歌迷回过头来，看到的都是同一个周杰伦。”时间过得太快像一路向北的龙卷风你把自己的青春献给所有爱你的人感谢这个时代让我遇见了最好的JAY周杰伦杰伦你曾说：我顶着大太阳，只想为你撑伞。杰伦，而我如今对你说：我顶着黑眼圈，只等你新歌。  指法芬芳张大仙z        2067     0 2019-09-16 23:12:42           2279758469         0
16588           27255356511568646686                                                                                                                                              他是歌手他是演员他是导演他是原创音乐人他是词曲创作人他是音乐制作人他非常的善良，他在当时的2008年汶川大地震捐了4200万他非常的有爱心，他经常关爱小动物他非常的有才华他是世界十大鬼才之一；他唱歌非常好听他

In [62]:
trace1 = go.Scatter(
    x=praise_count.nick,
    y=praise_count.praise_num,
    text=praise_count.praise_num,
    textposition='top center',
    hovertext=praise_count.content,
    mode="markers+text",
    textfont=dict(size=14),
    marker=dict(
        size=praise_count.praise_num.apply(np.sqrt),
        color=[i for i in range(praise_count.shape[0])],
        colorscale='Viridis',
        symbol=symbol_list,
        opacity=0.5,
    )
)
data = [trace1]
layout = go.Layout(
    template='ggplot2',
    images=qq_music_logo,
    title="评论获点赞数To榜",
    yaxis=dict(title='点赞数'))

fig = go.Figure(data=data, layout=layout)
fig.show()

点赞数最高的一条评论达到一万八千多条，是 陈 的评论：
>如果有一天 我带你去看周杰伦的演唱会 那么你一定对我很重要 因为我带你去看的 是我一整个青春

接下来是达到一万条，是 白 的评论：
>见过让一个软件崩服务器的人吗？他就是周杰伦！出道19年发一个曲子依旧火爆的周杰伦，音乐皇帝！

### 按天汇总评论

In [39]:
days_count = pd.DataFrame(comments_df.time.dt.strftime(
    "%Y-%m-%d").value_counts().sort_index())
days_count = days_count.rename(columns={"time": "counts"})
days_count.T

2019-09-16  2019-09-17  2019-09-18  2019-09-19  2019-09-20  2019-09-21  2019-09-22  2019-09-23
counts       11916        5724         839         418         312         243         214         104

In [40]:
trace1 = go.Scatter(
    x=days_count.index,
    y=days_count.counts.to_list(),
    text=days_count.counts.to_list(),
    textposition=['top right']+['top center'] *
    (days_count.shape[0]-2)+['top left'],
    mode="markers+text",
    marker=dict(
        size=10,
    ),
    fill='tozeroy'
)
data = [trace1]
layout = go.Layout(
    template='ggplot2',
    images=qq_music_logo,
    title="按日期统计评论数",
    yaxis=dict(title='评论数'),
)

fig = go.Figure(data=data, layout=layout)


fig.show()

### 按小时汇总评论

In [41]:
hours_count = pd.DataFrame(comments_df.time.dt.strftime(
    "%H").value_counts().sort_index())
hours_count = hours_count.rename(columns={"time": "counts"})
hours_count.T

00   01   02  03  04  05   06   07   08   09   10   11   12   13   14   15   16   17   18   19   20   21   22     23
counts  1692  416  175  74  66  80  129  298  401  543  481  392  401  345  282  256  231  243  214  237  223  235  254  12102

In [42]:
trace1 = go.Scatter(
    x=hours_count.index,
    y=hours_count.counts.to_list(),
    text=hours_count.counts.to_list(),
    textposition=['top right']+['top center'] *
    (hours_count.shape[0]-2)+['top left'],
    mode="markers+text",
    marker=dict(
        size=10,
    ),
    fill='tozeroy'
)
data = [trace1]
layout = go.Layout(
    template='ggplot2',
    images=qq_music_logo,
    title="按小时统计评论数",
    yaxis=dict(title='评论数'),
    xaxis=dict(
        tickmode='linear',
        ticktext=[f'{i:02d}' for i in range(23)],
        tickson='boundaries',
    ),
    grid=dict(
        domain=dict(x=[0.5, 0.6]))
)

fig = go.Figure(data=data, layout=layout)
fig.show()

因为周董16日23点发的专辑，所以16日这一天，以及23点的评论量都遥遥领先与其他日期，其他时间。

### 最早的评论

In [43]:
earliest = comments_df.sort_values(by='time', ascending=True)[['time','content','nick']]
# 过滤掉一些占座的（自付小于10）
earliest[earliest.content.map(len) > 10].head(10)

time                                                                                                                  content        nick
19769 2019-09-16 23:04:22                                                                                 满怀期待等候多时并且重新下回了qq音乐就是为了此时此刻第一时间来听我伦新歌！！！          小懒
19764 2019-09-16 23:04:24                                                                               如果有一天我带你去看周杰伦的演唱会那么你一定对我很重要因为我带你去看的是我一整个青春           陈
19763 2019-09-16 23:04:25  等了这么久，终于等到了今天，虽然不是新专但我也一样心满意足，是鸽鸽让我爱上音乐，让我也想和他一样弹钢琴，也是鸽鸽教我要听妈妈的话。我从三岁开始听杰伦的歌，如果说人生中的老师有三个，那么我人生中的老师就是爸妈和杰伦以及让我变得更好的老师们！         伽蓝雨
19753 2019-09-16 23:04:32                                                                                            拉风陪你追周杰伦，说好沙发！11月长沙站见。杰伦，我爱你！     周杰伦的小迷弟
19745 2019-09-16 23:04:36                                                                                                         大爱，我是1楼？？？还是那个味道     社会主意一块砖
19734 2019-09-16 23:04:38                                      经历了这么久的等待好像已经忘记了在等待什么曾经的少年也过了而立在那一首首的歌里还总能回忆起少年的你，少年的我已经不是在等待什么只是有些话，有些事情在回忆中更美好...  Mr.Deep...
19738 2019-09-16 23:04:38                                                                                                           为我伦打call！！！！！！     槑(⊙o⊙)…
19726 2019-09-16 23:04:40                                                                                                        啊啊啊第一时间！！终于进来了！！！         猫一只
19725 2019-09-16 23:04:40                                                                                                             挤不进来啊！挤不进来啊？         回口回
19711 2019-09-16 23:04:43                                                                                                             周杰伦，我喜欢你一辈子。           白

最早的评论由 小懒 同学发于 2019-09-16 23:04:22：
>满怀期待等候多时并且重新下回了qq音乐就是为了此时此刻第一时间来听我伦新歌！！！

### 回复评论分析

统计带有回复的评论个数

In [44]:
reply_value_counts = pd.DataFrame(comments_df.reply.value_counts())
reply_value_counts['comment_id'] = reply_value_counts.index
reply_value_counts = reply_value_counts.rename(columns={'reply': 'reply_num'})
reply_value_counts.head()

reply_num            comment_id
0                         18109                     0
3732625331568646264         129   3732625331568646264
27255356511568646699        112  27255356511568646699
19721474481568646488         64  19721474481568646488
11705604731568702517         58  11705604731568702517

将这些带有回复的评论单独取出来

In [45]:
root_comment_by_reply = comments_df.loc[comments_df.comment_id.isin(
    reply_value_counts['comment_id'])]
root_comment_by_reply.head()

comment_id               content       nick  praise_num reply                time     user_id vip_level
25   8796406631569221308             殿堂级唱片，牛批！         落梅           1     0 2019-09-23 14:48:28   879640663         0
62  15999134891569208602              说好不哭说好不哭        吴梓辉           0     0 2019-09-23 11:16:42  1599913489         3
73   8740668591569202565    林俊杰还是干不过周杰伦啊，排他后面了  不忘初心，方得始终           0     0 2019-09-23 09:36:05   874066859         0
85   9786822701569184724  你见过一个人发歌能把腾讯股价提个点的人吗       阿伟死了           2     0 2019-09-23 04:38:44   978682270         6
88   3937417951569181864   我终于开通了绿钻，终于能听我周董的歌了      若水◕‿-           1     0 2019-09-23 03:51:04   393741795         1

将 `comment_id` 和 `reply_num` 整合在一起，只显示回复数大于10的结果

In [46]:
reply_count = pd.merge(root_comment_by_reply[['comment_id', 'nick', 'content']],
                       reply_value_counts, how='left', on='comment_id').sort_values(by='reply_num', ascending=False)

In [47]:
reply_count = reply_count[reply_count.reply_num > 10]
reply_count

comment_id        nick                                                                                                                                                                                                                                                                                                       content  reply_num
588            3732625331568646264           陈                                                                                                                                                                                                                                                                    如果有一天我带你去看周杰伦的演唱会那么你一定对我很重要因为我带你去看的是我一整个青春        129
551           27255356511568646699          李现                                                                                                                                                  你知道吗？周董…多少人为了你开通了QQ音乐的绿砖多少人在你的新歌发布之前不换网名不改个性签名不换头像多少人为了你等到什么时候都愿意你是多少人的青春你是多少人的偶像你是多少人的期盼你是多少人愿意守护的人你又是多少人的希望又有多少人一直爱着你又有多少人一直等着你无论别人是谁无论别人喜欢谁我不管……我喜欢的是，周杰伦        112
577           19721474481568646488           白                                                                                                                                                                                                                                                                见过让一个软件崩服务器的人吗？他就是周杰伦！出道19年发一个曲子依旧火爆的周杰伦，音乐皇帝！         64
162           11705604731568702517          祁叔                                                                                                                                                                                                                                                                                             我的青春不是周杰伦………。是艾薇儿         58
542           22797584691568646762    指法芬芳张大仙z                                         当篮球从手中滑落，当练习滑板一次次摔倒，是你让我疲惫心灵得到短暂休憩；当每个失眠的深夜，是你带给我温暖，让我陷入最美好的梦想；当第一次牵起等我下课的女孩，是你的音乐带给我最甜蜜的浪漫，如果说最难忘的是谁？那么就是我永远无法抹去的记忆！一直也忘不了你说的那句：“不管什么时候，什么地点，我希望我的歌迷回过头来，看到的都是同一个周杰伦。”时间过得太快像一路向北的龙卷风你把自己的青春献给所有爱你的人感谢这个时代让我遇见了最好的JAY周杰伦杰伦你曾说：我顶着大太阳，只想为你撑伞。杰伦，而我如今对你说：我顶着黑眼圈，只等你新歌。         53
426            5509051321568647651         村花🌹                                                                                                                                                                                                                                                                     已经超越不了过去的经典著作了，这首歌没有很惊艳。而且感觉后半部分声音都不像我伦的了         22
1             15999134891569208602         吴梓辉                                                                                                                                                                                                                                                                                                      说好不哭说好不哭         22
587           27172464991568646265         伽蓝雨                                                                                                                                                                                       等了这么久，终于等到了今天，虽然不是新专但我也一样心满意足，是鸽鸽让我爱上音乐，让我也想和他一样弹钢琴，也是鸽鸽教我要听妈妈的话。我从三岁开始听杰伦的歌，如果说人生中的老师有三个，那么我人生中的老师就是爸妈和杰伦以及让我变得更好的老师们！         19
368           22797584691568648528    指法芬芳张大仙z                                                                                                                                  “何为我伦？”“傲娇公主·奶茶男孩。。”“可否具体？”“看似佛系，撒娇卖萌。”“可否再具体？”“无与伦比，哎呦，不错哦！”╭══╮┌══════════┐╭╯前面让开║地表最强---周杰伦专辑火爆专车╰⊙═⊙╯╰══⊙════⊙══╯吾之所爱---周杰伦愿你平安健康，愿你一直傲娇，愿你一切安好，愿你眼里皆是笑意.我们一直都在，做你永远的听众。         19
581           33415886211568646369       💎九局下半                                                                                                 万众瞩目，看看谁回来了称他为现象级歌手都不过分，粉丝最起码涵盖80后到00后三个年龄段，甚至包括好多成名了的艺人，前段时间随便给后辈玩玩，一号召一堆人给他打榜，甚至包括各种明星！流行歌手不敢说，我就知道当初有好多现在成名了的说唱歌手，有13都是因为听了他的歌才决定玩说唱的我就不用说了，永远忘不了曾经攒下午饭钱买他卡带的日子说好不哭，有新歌我们肯定不哭，只要你周杰伦发了新歌，我绝对第一时间支持，respect         19
557           27255356511568646686          李现                  

In [48]:
trace1 = go.Bar(
    x=reply_count.nick,
    y=reply_count.reply_num,
    text=reply_count.reply_num,
    hovertext=reply_count.content,
    textposition='outside',
)
data = [trace1]
layout = go.Layout(template='ggplot2',
                   images=qq_music_logo,
                   title="被回复的评论Top榜",
                   yaxis=dict(title='回复量'),
                   )

fig = go.Figure(data=data, layout=layout)
fig.show()

回复最多的是昵称为 **陈** 的这位用户，评论内容为：
>如果有一天 我带你去看周杰伦的演唱会 那么你一定对我很重要 因为我带你去看的 是我一整个青春

下面我们看下这条评论的回复都有哪些内容

In [49]:
temp = comments_df[comments_df.reply == '3732625331568646264'].sort_values(
    by='praise_num', ascending=False).sample(10)
temp[temp.content.map(len) > 1][['content','nick']]

content         nick
4754                                        首先你要买到票      fangxin
2524                          如果有一天你抢到门票，那么你运气一定很好。           Dd
18021                    不带这样，为了攒这样，说你是不是歌都没听完就评论了。        隔壁W师傅
113                                        说的太好了！真的         黯然无恙
3189   如果有一天，我带你去看周杰伦的演唱会，那么我一定想要嫁给你，因为我带着你走过了我的前半生  YoGa · 兔洋洋🐰
11904                                     我都大学了来不及了      Lzy.Jay
2547                  我家老唐看你的评论看哭了······你说出了他想说的话啊！         小唐同学
2884                           难道不是因为杰伦演唱会的黄牛票都挺贵吗？       yellow
669                                        抢不到票，下一个    爱吃萝卜的大白鹅.
11562                              不是你一个人是这样的想法，与同。       Feb  z

### 单个用户评论数量

In [63]:
user_value_counts = pd.DataFrame(comments_df.user_id.value_counts())
user_value_counts = user_value_counts.rename(
    columns={'user_id': 'comments_num'})
user_value_counts['user_id'] = user_value_counts.index
user_value_counts.head()

comments_num              user_id
1599913489                     38           1599913489
229930621                      37            229930621
1769897486                     30           1769897486
1170560473                     29           1170560473
1152921504623060237            25  1152921504623060237

为了合并上面的统计结果，将每个用户只保留第一条评论。

In [64]:
users_df_uni = comments_df.drop_duplicates(['user_id'], keep="first")
users_df_uni.head()

comment_id                                                content      nick  praise_num                 reply                time              user_id vip_level
0           15951140991569230663                                                    123      路过蜻蜓           0                     0 2019-09-23 17:24:23           1595114099         1
1           15999134891569230439                                               拜托别说那没用的       吴梓辉           0  15999134891569208602 2019-09-23 17:20:39           1599913489         3
6  11529215049586869761569230245                                                    我爱你       杨汝兰           0                     0 2019-09-23 17:17:25  1152921504958686976         1
7  11529215046110398451569228993           小哥哥说，一定带我去找你，听你的演唱会，可是总是抢不到票，那么多人和我爱着你，你开心不！  故事De小黄花🌸           1                     0 2019-09-23 16:56:33  1152921504611039845         0
8  11529215047402599471569228876  明明是一首说好不哭的歌，听了旋律想哭，看了mv想哭，读了歌词想哭。想唱，却怎么都唱不好这首歌，开口就落泪了    旋木音乐艺术           1                     0 2019-09-23 16:54:36  1152921504740259947         0

In [65]:
user_count = pd.merge(users_df_uni[['user_id', 'nick', 'content']],
                      user_value_counts, how='left', on='user_id').sort_values(by='comments_num', ascending=False)

user_count = user_count[user_count.comments_num > 10]
user_count

user_id       nick                                                                       content  comments_num
1               1599913489        吴梓辉                                                                      拜托别说那没用的            38
118              229930621      ﹎_╋﹎_                                                                    太好听了，越听越好听            37
2621            1769897486        怪蜀黍  蔡徐坤人均多少张周杰伦人均多少张周杰伦第一名才买了不到2万块蔡徐坤第一名多少你买一张周杰伦单曲看看你排第几名你买一张蔡徐坤看坎排第几名憨p你母亲还健在？            30
2619            1170560473         祁叔                                                                    憨比，你父亲昨天健在            29
834    1152921504623060237    🔆Lee欢喜🌫                                                                         多听几次嘛            25
268               18240309        金鍂鑫                                                             他认为有意义的事就是宠妻晒娃喝奶茶            21
546             1260526087   蜕变※这一刻开始                                                              没事，买专辑听歌已经是最好的支持            14
1896            2997670981        Jay                                                                  我上一条评论就是这么说的            13
57     1152921504764772824        童可可                                                                     我那時候買的是5塊            13
270             1992945782  依然饭特稀plus                                                                          就这样吧            12
11132           1635040891         你.                   真的特别特别喜欢跟现在的音乐人不一样的是喜欢当年你出场的时候那种胆怯紧张而现在的人好像太优秀了没有紧张什么都做得很好.            12
27              1459207257    Mr's布朗森                                                                      两万我来了，加油            12
552    1152921504914187150         陳晨                                                                 你两张我两张明天榜单就姓周            11
10403           1345810321      差不多先生                                                                      还可以吧，有点短            11

﹎_╋﹎_ 这位用户个人贡献值最大，达到了35条。
我们随机拿5条，看他都评论了什么内容。

In [66]:
comments_df[comments_df.user_id == '229930621'].sample(5)

comment_id                                                                                  content   nick  praise_num                 reply                time    user_id vip_level
1173  2299306211568860336                                                                                引战的举报就完事了  ﹎_╋﹎_           0   9848297731568798852 2019-09-19 10:32:16  229930621         0
495   2299306211569033490                                                                                      周杰伦  ﹎_╋﹎_           0                     0 2019-09-21 10:38:10  229930621         0
767   2299306211568953554                                                                                       好听  ﹎_╋﹎_           0                     0 2019-09-20 12:25:54  229930621         0
1338  2299306211568817343  其实这首歌是写给歌迷的，虽然不在江湖，却还有大家护着他，等着他，为他加油，甚至为他不在微博也把超话刷到NO1，谢谢大家，但是可能已经慢慢离开，因为超人不会飞，超人不能流眼泪。  ﹎_╋﹎_           2                     0 2019-09-18 22:35:43  229930621         0
924   2299306211568901834                                                                我是老粉，开始不觉得，多循环几次就入了迷，太好听了  ﹎_╋﹎_           2  11421324271568901531 2019-09-19 22:03:54  229930621         0

In [67]:
trace1 = go.Bar(
    y=user_count.nick[::-1],
    x=user_count.comments_num[::-1],
    text=user_count.comments_num[::-1],
    textposition='outside',
    hovertext=user_count.content[::-1],
    orientation='h',
)
data = [trace1]
layout = go.Layout(template='ggplot2',
                   images=qq_music_logo,
                   title="单个用户评论量",
                   yaxis=dict(title='评论量'),
                   )

fig = go.Figure(data=data, layout=layout)
fig.show()

### VIP分布

In [69]:
vip_count = pd.DataFrame(users_df_uni.vip_level.value_counts())
vip_count = vip_count.rename(columns={'vip_level': 'counts'})
vip_list = [f"VIP{i}" for i in vip_count.index]
vip_list[0] = "普通"
vip_count.index = vip_list
vip_count

counts
普通     11116
VIP1    1360
VIP2    1201
VIP6     960
VIP3     915
VIP5     604
VIP4     448
VIP7     165
VIP8     156

In [70]:
trace1 = go.Scatter(
    x=vip_count.index,
    y=vip_count.counts,
    text=vip_count.counts,
    textposition='top center',
    mode="markers+text",
    marker=dict(
        size=20,
        color='#2CB56B'
    )
)
data = [trace1]
layout = go.Layout(
    template='ggplot2',
    images=qq_music_logo,
    title="VIP分布",
    yaxis=dict(title='用户量'),
)

fig = go.Figure(data=data, layout=layout)
fig.show()

In [71]:
vip_count[1::].sum()

counts    5809
dtype: int64

可以看出，拥有尊贵的VIP身份的用户是普通用户的一半左右。

## 总结

以上即为本次分析的一些内容，主要是以评论为目的，从时间，用户，点赞量，回复量，emoji表情，VIP等级，分词等几个维度看了下《说好不哭》QQ音乐的2万条评论。
本次爬虫时间和精力都花了很多，整体过程也是挺费劲的，数据可视化全部用Plotly库，绘制的图有很强的交互性，也更好看。QQ音乐爬取数据的过程不难，因为数据全部都可以找到json来源，分析过程中温习了一遍Pandas常见的一些功能。